In [19]:
from mesh_dataset_utils import *
from mesh_experiment import Experiment
import trimesh

from sklearn.model_selection import train_test_split
from datetime import datetime
import torch
from MLP import MLP
from torch import nn
from visualization import *

In [ ]:
MESH_NAME = 'Spikeyball1'
MESH_DIR = f'meshes/{MESH_NAME}.stl'
mesh = trimesh.load(MESH_DIR)
mesh.show()

In [ ]:
smooth_type = 'taubin'
smooth_iter = 30000
dataset_type='norm'
dataset, smooth = build_norms_dataset(mesh, smooth_iter=smooth_iter, smooth_type=smooth_type)

In [4]:
smooth.show()

In [2]:
DATASET_NAME = f'{MESH_NAME}_{smooth_type}_{smooth_iter}'
np.savez(f'npz_train/{DATASET_NAME}', fourier=dataset['fourier'], points=dataset['points'], target=dataset['target'])

NameError: name 'MESH_NAME' is not defined

In [111]:
DATASET_NAME = 'crinkleball_lap_3000_offset'
dataset = np.load(f'npz_train/{DATASET_NAME}.npz')

In [112]:
print(dataset.files)

['fourier', 'points', 'target']


In [113]:
X = dataset['fourier']
y = dataset['target']

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.15, random_state=11)


batch_size = 1000
train_data = torch.utils.data.TensorDataset(torch.tensor(X_train).float(), torch.tensor(y_train).float())
train_loader = torch.utils.data.DataLoader(train_data, batch_size=batch_size, shuffle=True)

test_data = torch.utils.data.TensorDataset(torch.tensor(X_test).float(), torch.tensor(y_test).float())
test_loader = torch.utils.data.DataLoader(test_data, batch_size=batch_size, shuffle=True)

In [114]:
model = MLP(
            input_dim=X.shape[1],
            output_dim=y.shape[1],
            hidden_dim=512,
            n_layers=6,
            geometric_init=True,
            beta=True,
            sine=True,
            all_sine=True,
            skip=True,
            bn=True,
            dropout=0.0
            )

In [115]:
lr=1e-4
optimizer = torch.optim.Adam(model.parameters(), lr=lr)
loss_fn = nn.MSELoss()
epochs = 20
rand_inits = 2
now = datetime.now()

OUT_DIR = f'experiments/{now.strftime("%m_%d_%y_%H:%M:%S")}_{DATASET_NAME}'
model_info = {'experiment notes': 'first surface norms experiment'}

In [116]:
exp = Experiment(model,
                    optimizer,
                    loss_fn,
                    train_loader,
                    test_loader,
                    epochs,
                    rand_inits,
                    OUT_DIR,
                    model_info,
                    rand_seed=11)

In [117]:
log = exp.run()


started training for 20 epochs
epoch 0 training loss: 0.7505680084228515 eval loss: 0.4874379634857178
epoch 5 training loss: 0.008273387806756155 eval loss: 0.01484223734587431
epoch 10 training loss: 0.002691943304879325 eval loss: 0.002177509479224682
epoch 15 training loss: 0.0023796077285494124 eval loss: 0.0017169076018035412
started training for 20 epochs
epoch 0 training loss: 0.4549637385777065 eval loss: 0.11143666505813599
epoch 5 training loss: 0.004045865365437099 eval loss: 0.0017436654306948185
epoch 10 training loss: 0.0033427340643746514 eval loss: 0.0026604412123560905
epoch 15 training loss: 0.002809189898627145 eval loss: 0.001845759223215282


In [120]:
losses=[]
for i in log['train_results']:
    losses.append(i['best_loss'])

In [121]:
best_state_path = f'experiments/{now.strftime("%m_%d_%y_%H:%M:%S")}_{DATASET_NAME}/run_{log["best_rand_init"]}/best-model-parameters.pt'

In [139]:
inference_X = dataset['fourier']
preds = model(torch.tensor(inference_X).float())
preds = preds.detach().numpy()
preds_mat = preds.reshape((-1, 3, 3))



In [136]:
new_pts = np.zeros((dataset['points'].shape[0], 3))
new_norms = np.zeros((dataset['points'].shape[0], 3))

preds = np.zeros((dataset['points'].shape[0],6))

for i in range(dataset['points'].shape[0]):
    preds[i,:] = dataset['points'][i,:].dot(preds_mat[i])

new_pts = preds[:, 3:]
blank = get_sphere(size=3)

ValueError: could not broadcast input array from shape (3,) into shape (6,)

In [124]:
inference_2 = trimesh.Trimesh(vertices=new_pts, faces=dataset['faces'])

KeyError: 'faces is not a file in the archive'

In [85]:
print(dataset.files)

['fourier', 'points', 'faces', 'target']


In [86]:
data=visualization(mesh, smooth, smooth_type,DATASET_NAME,dataset_type,losses,inference_2)

NameError: name 'mesh' is not defined

In [87]:
inference_2.show()

In [88]:
smooth.vertices = new_pts

NameError: name 'smooth' is not defined

In [89]:
garbage = smooth.export(f'experiments/{now.strftime("%m_%d_%y_%H:%M:%S")}_{DATASET_NAME}/run_{log["best_rand_init"]}/inference.stl')

NameError: name 'smooth' is not defined

In [90]:
loaded_inf = trimesh.load(f'experiments/{now.strftime("%m_%d_%y_%H:%M:%S")}_{DATASET_NAME}/run_{log["best_rand_init"]}/inference.stl')

ValueError: string is not a file: experiments/04_24_23_18:03:08_Spikeyball1_lap_3000_norm/run_1/inference.stl

In [35]:
loaded_inf.show()